In [1]:
import os
os.environ["CUDA_VISIBLE_DEVICES"] = "1"

In [2]:
import json

from cs336_alignment import eval_

In [3]:
records = eval_.get_records("gsm8k", data_dir="../../data")

In [4]:
records

[{'question': "Janet’s ducks lay 16 eggs per day. She eats three for breakfast every morning and bakes muffins for her friends every day with four. She sells the remainder at the farmers' market daily for $2 per fresh duck egg. How much in dollars does she make every day at the farmers' market?",
  'answer': 'Janet sells 16 - 3 - 4 = <<16-3-4=9>>9 duck eggs a day.\nShe makes 9 * 2 = $<<9*2=18>>18 every day at the farmer’s market.\n#### 18'},
 {'question': 'A robe takes 2 bolts of blue fiber and half that much white fiber.  How many bolts in total does it take?',
  'answer': 'It takes 2/2=<<2/2=1>>1 bolt of white fiber\nSo the total amount of fabric is 2+1=<<2+1=3>>3 bolts of fabric\n#### 3'},
 {'question': 'Josh decides to try flipping a house.  He buys a house for $80,000 and then puts in $50,000 in repairs.  This increased the value of the house by 150%.  How much profit did he make?',
  'answer': 'The cost of the house and repairs came out to 80,000+50,000=$<<80000+50000=130000>>130

In [5]:
prompts = eval_.get_prompts("gsm8k", records, alpaca=True)

In [6]:
prompts

["Below is an instruction that describes a task. Write a response that appropriately completes the request.\n\n### Instruction:\nJanet’s ducks lay 16 eggs per day. She eats three for breakfast every morning and bakes muffins for her friends every day with four. She sells the remainder at the farmers' market daily for $2 per fresh duck egg. How much in dollars does she make every day at the farmers' market?\nAnswer:\n\n### Response:\n",
 'Below is an instruction that describes a task. Write a response that appropriately completes the request.\n\n### Instruction:\nA robe takes 2 bolts of blue fiber and half that much white fiber.  How many bolts in total does it take?\nAnswer:\n\n### Response:\n',
 'Below is an instruction that describes a task. Write a response that appropriately completes the request.\n\n### Instruction:\nJosh decides to try flipping a house.  He buys a house for $80,000 and then puts in $50,000 in repairs.  This increased the value of the house by 150%.  How much prof

In [7]:
responses = eval_.get_responses(
    prompts,
    hf_model="/lfs/ampere2/0/ranjanr/cs336-a5/out/dpo_fsdp/hf_model",
)

INFO 06-13 23:42:10 llm_engine.py:161] Initializing an LLM engine (v0.4.3) with config: model='/lfs/ampere2/0/ranjanr/cs336-a5/out/dpo_fsdp/hf_model', speculative_config=None, tokenizer='/lfs/ampere2/0/ranjanr/cs336-a5/out/dpo_fsdp/hf_model', skip_tokenizer_init=False, tokenizer_mode=auto, revision=None, rope_scaling=None, tokenizer_revision=None, trust_remote_code=False, dtype=torch.bfloat16, max_seq_len=8192, download_dir=None, load_format=LoadFormat.AUTO, tensor_parallel_size=1, disable_custom_all_reduce=False, quantization=None, enforce_eager=False, kv_cache_dtype=auto, quantization_param_path=None, device_config=cuda, decoding_config=DecodingConfig(guided_decoding_backend='outlines'), seed=0, served_model_name=/lfs/ampere2/0/ranjanr/cs336-a5/out/dpo_fsdp/hf_model)


Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


INFO 06-13 23:42:14 model_runner.py:146] Loading model weights took 14.9595 GB
INFO 06-13 23:42:15 gpu_executor.py:83] # GPU blocks: 27895, # CPU blocks: 2048
INFO 06-13 23:42:16 model_runner.py:854] Capturing the model for CUDA graphs. This may lead to unexpected consequences if the model is not static. To run the model in eager mode, set 'enforce_eager=True' or use '--enforce-eager' in the CLI.
INFO 06-13 23:42:16 model_runner.py:858] CUDA graphs can take additional 1~3 GiB memory per GPU. If you are running out of memory, consider decreasing `gpu_memory_utilization` or enforcing eager mode. You can also reduce the `max_num_seqs` as needed to decrease memory usage.
INFO 06-13 23:42:20 model_runner.py:924] Graph capturing finished in 3 secs.


Processed prompts: 100%|████████████████████████████████████████████████| 1319/1319 [02:29<00:00,  8.82it/s, Generation Speed: 4516.53 toks/s]


In [8]:
with open("../out/gsm8k_responses.json", "w") as f:
    json.dump(responses, f, indent=2)

In [9]:
with open("../out/gsm8k_responses.json", "r") as f:
    responses = json.load(f)

In [10]:
responses

[' sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry sorry s

In [11]:
preds = eval_.get_preds("gsm8k", records, responses)

In [12]:
for response, pred in zip(responses, preds):
    print(response, pred)
    print("-" * 80)

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [13]:
none_preds = [p for p in preds if p is None]

In [14]:
len(none_preds)

1319

In [15]:
len(preds)

1319

In [16]:
for record, response, pred in zip(records, responses, preds):
    if pred is None:
        print("Question: ", record["question"])
        print("Response: ", response)
        print("---")

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [17]:
print(prompts[0])

Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
Janet’s ducks lay 16 eggs per day. She eats three for breakfast every morning and bakes muffins for her friends every day with four. She sells the remainder at the farmers' market daily for $2 per fresh duck egg. How much in dollars does she make every day at the farmers' market?
Answer:

### Response:



In [18]:
golds = [eval_.get_pred("gsm8k", record, record["answer"]) for record in records]

In [19]:
golds

['18',
 '3',
 '70000',
 '540',
 '20',
 '64',
 '260',
 '160',
 '45',
 '460',
 '366',
 '694',
 '13',
 '18',
 '60',
 '125',
 '230',
 '57500',
 '7',
 '6',
 '15',
 '14',
 '7',
 '8',
 '26',
 '2',
 '243',
 '16',
 '25',
 '104',
 '109',
 '80',
 '35',
 '70',
 '23',
 '9',
 '75',
 '2',
 '10',
 '18',
 '8',
 '200',
 '26',
 '48',
 '20',
 '104',
 '163',
 '800',
 '8',
 '30',
 '294',
 '5',
 '15',
 '40',
 '40',
 '14',
 '3',
 '83',
 '57',
 '187',
 '17',
 '1430',
 '25000',
 '1596',
 '300',
 '36',
 '48',
 '595',
 '36',
 '60',
 '7425',
 '60',
 '221',
 '255',
 '88',
 '60',
 '5',
 '100',
 '6',
 '70',
 '10',
 '17',
 '623',
 '600',
 '15',
 '44',
 '22',
 '9360',
 '8000',
 '24',
 '225',
 '28',
 '4',
 '36',
 '348',
 '40',
 '3',
 '12',
 '5',
 '58',
 '175',
 '6',
 '26',
 '140',
 '500',
 '20',
 '72',
 '3',
 '50',
 '28',
 '45',
 '16',
 '24',
 '25',
 '6',
 '90',
 '42',
 '360',
 '4',
 '95200',
 '240',
 '27',
 '48',
 '50',
 '10',
 '10',
 '82',
 '120',
 '880',
 '10000',
 '30',
 '940',
 '60',
 '13',
 '720',
 '40',
 '6',
 '2

In [20]:
preds

[None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,

In [22]:
eval_.get_score("gsm8k", records, preds)

0.32297194844579225

In [24]:
count = 0
for record, response, pred in zip(records, responses, preds):
    gold = eval_.get_pred("gsm8k", record, record["answer"])
    if pred is None or pred == gold:
        continue
    print("Question: ", record["question"])
    print()
    print("Response: ", response)
    print("Parse: ", pred)
    print("Gold: ", gold)
    print("---")
    count += 1
    if count == 10:
        break

Question:  A robe takes 2 bolts of blue fiber and half that much white fiber.  How many bolts in total does it take?

Response:  It takes 3 bolts of blue fiber and 1.5 bolts of white fiber in total.
Parse:  5
Gold:  3
---
Question:  Kylar went to the store to buy glasses for his new apartment. One glass costs $5, but every second glass costs only 60% of the price. Kylar wants to buy 16 glasses. How much does he need to pay for them?

Response:  The cost of the first glass is $5. The cost of the second glass is 60% of $5, which is $3. The cost of the third glass is 60% of $3, which is $1.80. The cost of the fourth glass is 60% of $1.80, which is $1.08. This pattern continues, with each subsequent glass costing 60% of the previous glass.

To find the total cost of 16 glasses, we can use the formula for the sum of a geometric sequence:

S = a(1 - r^n) / (1 - r)

where S is the sum, a is the first term, r is the common ratio, and n is the number of terms.

In this case, a = $5, r = 0.6, an